 # Table of Contents
<div class="toc" style="margin-top: 1em;"><ul class="toc-item" id="toc-level0"></ul></div>

In [ ]:
# this script is designed to run on linux and mac only, system calls to windows will fail(!)
# sourcing or executing this script in an open R session will generate the normalized gene expression
# matrices used for batch correction, along with the appropriate meta data for each study.

In [5]:
library(scran)
library(biomaRt)
library(limSolve)
library(scater)
library(SingleCellExperiment)

Loading required package: ggplot2

Attaching package: ‘ggplot2’

The following object is masked from ‘package:limSolve’:

    resolution


Attaching package: ‘scater’

The following object is masked from ‘package:S4Vectors’:

    rename

The following object is masked from ‘package:stats’:

    filter



In [6]:
##############
## GSE81076 ##
##############
# download file from GEO
gse81076 <- 'GSE81076_D2_3_7_10_17.txt.gz'
if (!file.exists(gse81076)) { download.file("ftp://ftp.ncbi.nlm.nih.gov/geo/series/GSE81nnn/GSE81076/suppl/GSE81076%5FD2%5F3%5F7%5F10%5F17%2Etxt%2Egz",gse81076)} 

In [7]:
gse81076.df <- read.table(gse81076, sep='\t', h=T, stringsAsFactors=F)
gse81076.ndim <- dim(gse81076.df)[2]

In [12]:
head(gse81076.df)
head((gse81076.df)[2])
gse81076.ndim

X               D2ex_1 D2ex_2   D2ex_3   D2ex_4 D2ex_5 D2ex_6 D2ex_7 D2ex_8
1 A1BG-AS1__chr19 0      0.000000 0.000000 0      0      0      0      0     
2 A1BG__chr19     0      0.000000 0.000000 0      0      0      0      0     
3 A1CF__chr10     0      2.007853 1.001958 0      0      0      0      0     
4 A2M-AS1__chr12  0      0.000000 0.000000 0      0      0      0      0     
5 A2ML1__chr12    0      0.000000 0.000000 0      0      0      0      0     
6 A2MP1__chr12    0      0.000000 0.000000 0      0      0      0      0     
  D2ex_9 ⋯ D17TGFB_87 D17TGFB_88 D17TGFB_89 D17TGFB_90 D17TGFB_91 D17TGFB_92
1 0      ⋯ 0          0.000000   0          0          0.000000   0.000000  
2 0      ⋯ 0          1.001958   0          0          0.000000   0.000000  
3 0      ⋯ 0          1.001958   0          0          1.001958   1.001958  
4 0      ⋯ 0          0.000000   0          0          0.000000   0.000000  
5 0      ⋯ 0          0.000000   0          0          0.000000   0.000000  
6 0      ⋯ 0          0.000000   0          0          0.000000   0.000000  
  D17TGFB_93 D17TGFB_94 D17TGFB_95 D17TGFB_96
1 0.000000   0.000000   0          0         
2 0.000000   0.000000   0          0         
3 1.001958   1.001958   0          0         
4 0.000000   0.000000   0          0         
5 0.000000   2.007853   0          0         
6 0.000000   0.000000   0          0

D2ex_1
1 0     
2 0     
3 0     
4 0     
5 0     
6 0

[1] 1729

In [13]:
# construct the meta data from the cell names
donor.names <- unlist(regmatches(colnames(gse81076.df)[2:gse81076.ndim],
                                 gregexpr(pattern="D[0-9]{1,2}", 
                                          colnames(gse81076.df)[2:gse81076.ndim])))

In [14]:
head(donor.names)

[1] "D2" "D2" "D2" "D2" "D2" "D2"

In [15]:
plate.id <- unlist(lapply(strsplit(unlist(lapply(strsplit(head(colnames(gse81076.df)[2:gse81076.ndim]),
                                                          split="D[0-9]{1,2}", perl=T), 
                                                 FUN=function(x) paste0(x[2]))),
                                   fixed=T, split="_"),
                          FUN=function(c) paste0(c[1])))

In [17]:
gse81076.ndim-1

[1] 1728

In [18]:
protocol.id <- rep('CELseq', gse81076.ndim-1)
study.id <- rep('GSE81076', gse81076.ndim-1)
gse81076.meta <- data.frame(list('Donor' = donor.names,
                                 'Plate' = plate.id,
                                 'Protocol' = protocol.id,
                                 'Study' = study.id,
                                 'Sample' = colnames(gse81076.df)[2:gse81076.ndim]))
rownames(gse81076.meta) <- colnames(gse81076.df)[2:gse81076.ndim]
colnames(gse81076.df) <- gsub(colnames(gse81076.df), pattern='X', replacement='gene')

In [19]:
head(gse81076.meta)

Donor Plate Protocol Study    Sample
D2ex_1 D2    ex    CELseq   GSE81076 D2ex_1
D2ex_2 D2    ex    CELseq   GSE81076 D2ex_2
D2ex_3 D2    ex    CELseq   GSE81076 D2ex_3
D2ex_4 D2    ex    CELseq   GSE81076 D2ex_4
D2ex_5 D2    ex    CELseq   GSE81076 D2ex_5
D2ex_6 D2    ex    CELseq   GSE81076 D2ex_6

In [20]:
# remove superfluous suffixes from gene IDs
gse81076.df$gene <- gsub(gse81076.df$gene,
                         pattern="__chr[0-9]+", replacement="")

In [24]:
head(gse81076.df$gene)
head(gse81076.df)

[1] "A1BG-AS1" "A1BG"     "A1CF"     "A2M-AS1"  "A2ML1"    "A2MP1"

gene     D2ex_1 D2ex_2   D2ex_3   D2ex_4 D2ex_5 D2ex_6 D2ex_7 D2ex_8 D2ex_9 ⋯
1 A1BG-AS1 0      0.000000 0.000000 0      0      0      0      0      0      ⋯
2 A1BG     0      0.000000 0.000000 0      0      0      0      0      0      ⋯
3 A1CF     0      2.007853 1.001958 0      0      0      0      0      0      ⋯
4 A2M-AS1  0      0.000000 0.000000 0      0      0      0      0      0      ⋯
5 A2ML1    0      0.000000 0.000000 0      0      0      0      0      0      ⋯
6 A2MP1    0      0.000000 0.000000 0      0      0      0      0      0      ⋯
  D17TGFB_87 D17TGFB_88 D17TGFB_89 D17TGFB_90 D17TGFB_91 D17TGFB_92 D17TGFB_93
1 0          0.000000   0          0          0.000000   0.000000   0.000000  
2 0          1.001958   0          0          0.000000   0.000000   0.000000  
3 0          1.001958   0          0          1.001958   1.001958   1.001958  
4 0          0.000000   0          0          0.000000   0.000000   0.000000  
5 0          0.000000   0          0          0.000000   0.000000   0.000000  
6 0          0.000000   0          0          0.000000   0.000000   0.000000  
  D17TGFB_94 D17TGFB_95 D17TGFB_96
1 0.000000   0          0         
2 0.000000   0          0         
3 1.001958   0          0         
4 0.000000   0          0         
5 2.007853   0          0         
6 0.000000   0          0

In [25]:
# remove the duplicated gene names
gse81076.df <- gse81076.df[!duplicated(gse81076.df$gene), ]

rownames(gse81076.df) <- gse81076.df$gene

In [26]:
# remove the gene ID column for downstream normalization
gse81076.df <- gse81076.df[, -1]

In [27]:
head(gse81076.df)

D2ex_1 D2ex_2   D2ex_3   D2ex_4 D2ex_5 D2ex_6 D2ex_7 D2ex_8 D2ex_9
A1BG-AS1 0      0.000000 0.000000 0      0      0      0      0      0     
A1BG     0      0.000000 0.000000 0      0      0      0      0      0     
A1CF     0      2.007853 1.001958 0      0      0      0      0      0     
A2M-AS1  0      0.000000 0.000000 0      0      0      0      0      0     
A2ML1    0      0.000000 0.000000 0      0      0      0      0      0     
A2MP1    0      0.000000 0.000000 0      0      0      0      0      0     
         D2ex_10 ⋯ D17TGFB_87 D17TGFB_88 D17TGFB_89 D17TGFB_90 D17TGFB_91
A1BG-AS1 0       ⋯ 0          0.000000   0          0          0.000000  
A1BG     0       ⋯ 0          1.001958   0          0          0.000000  
A1CF     0       ⋯ 0          1.001958   0          0          1.001958  
A2M-AS1  0       ⋯ 0          0.000000   0          0          0.000000  
A2ML1    0       ⋯ 0          0.000000   0          0          0.000000  
A2MP1    0       ⋯ 0          0.000000   0          0          0.000000  
         D17TGFB_92 D17TGFB_93 D17TGFB_94 D17TGFB_95 D17TGFB_96
A1BG-AS1 0.000000   0.000000   0.000000   0          0         
A1BG     0.000000   0.000000   0.000000   0          0         
A1CF     1.001958   1.001958   1.001958   0          0         
A2M-AS1  0.000000   0.000000   0.000000   0          0         
A2ML1    0.000000   0.000000   2.007853   0          0         
A2MP1    0.000000   0.000000   0.000000   0          0

In [28]:
# remove cells and genes with all 0's
gene_sparsity <- (apply(gse81076.df == 0, MARGIN = 1, sum)/dim(gse81076.df)[2])
keep_genes <- gene_sparsity < 0.9
gse81076.nz <- gse81076.df[keep_genes, ]

In [32]:
head(gse81076.nz)

D2ex_1 D2ex_2   D2ex_3   D2ex_4   D2ex_5   D2ex_6 D2ex_7   D2ex_8  
A1BG  0      0.000000 0.000000 0.000000 0.000000 0      0.000000 0.000000
A1CF  0      2.007853 1.001958 0.000000 0.000000 0      0.000000 0.000000
AACS  0      0.000000 0.000000 0.000000 1.001958 0      0.000000 0.000000
AAGAB 0      0.000000 1.001958 0.000000 0.000000 0      1.001958 1.001958
AAK1  0      2.007853 0.000000 3.017717 0.000000 0      2.007853 0.000000
AAMDC 0      0.000000 0.000000 0.000000 0.000000 0      0.000000 0.000000
      D2ex_9   D2ex_10  ⋯ D17TGFB_87 D17TGFB_88 D17TGFB_89 D17TGFB_90
A1BG  0.000000 0.000000 ⋯ 0.000000   1.001958   0.000000   0.000000  
A1CF  0.000000 0.000000 ⋯ 0.000000   1.001958   0.000000   0.000000  
AACS  1.001958 0.000000 ⋯ 1.001958   1.001958   0.000000   1.001958  
AAGAB 1.001958 1.001958 ⋯ 0.000000   2.007853   1.001958   1.001958  
AAK1  3.017717 2.007853 ⋯ 2.007853   4.031579   4.031579   1.001958  
AAMDC 0.000000 0.000000 ⋯ 1.001958   1.001958   0.000000   0.000000  
      D17TGFB_91 D17TGFB_92 D17TGFB_93 D17TGFB_94 D17TGFB_95 D17TGFB_96
A1BG  0.000000   0.000000   0.000000   0.000000   0.000000   0         
A1CF  1.001958   1.001958   1.001958   1.001958   0.000000   0         
AACS  2.007853   0.000000   0.000000   2.007853   0.000000   0         
AAGAB 0.000000   2.007853   0.000000   0.000000   0.000000   0         
AAK1  0.000000   2.007853   1.001958   2.007853   2.007853   0         
AAMDC 0.000000   1.001958   0.000000   0.000000   0.000000   0

In [33]:
cell_sparsity <- apply(gse81076.nz == 0, MARGIN = 2, sum)/dim(gse81076.nz)[1]
keep_cells <- cell_sparsity < 0.8
gse81076.nz <- gse81076.nz[, keep_cells]
gse81076.nz <- apply(gse81076.nz, 2, as.integer)

In [34]:
head(gse81076.nz)

D2ex_1 D2ex_2 D2ex_3 D2ex_4 D2ex_5 D2ex_6 D2ex_7 D2ex_8 D2ex_9 D2ex_10 ⋯
[1,] 0      0      0      0      0      0      0      0      0      0       ⋯
[2,] 0      2      1      0      0      0      0      0      0      0       ⋯
[3,] 0      0      0      0      1      0      0      0      1      0       ⋯
[4,] 0      0      1      0      0      0      1      1      1      1       ⋯
[5,] 0      2      0      3      0      0      2      0      3      2       ⋯
[6,] 0      0      0      0      0      0      0      0      0      0       ⋯
     D17TGFB_86 D17TGFB_87 D17TGFB_88 D17TGFB_89 D17TGFB_90 D17TGFB_91
[1,] 0          0          1          0          0          0         
[2,] 1          0          1          0          0          1         
[3,] 0          1          1          0          1          2         
[4,] 2          0          2          1          1          0         
[5,] 2          2          4          4          1          0         
[6,] 0          1          1          0          0          0         
     D17TGFB_92 D17TGFB_93 D17TGFB_94 D17TGFB_95
[1,] 0          0          0          0         
[2,] 1          1          1          0         
[3,] 0          0          2          0         
[4,] 2          0          0          0         
[5,] 2          1          2          2         
[6,] 1          0          0          0

In [35]:
# use the spike in genes to estimate size factors for normalization
# all values show be non-negative integers
spikes <- grepl(rownames(gse81076.df[keep_genes, ]),
                pattern='ERCC')

In [36]:
head(spikes)

[1] FALSE FALSE FALSE FALSE FALSE FALSE

In [37]:
sce <- SingleCellExperiment(list(counts = as.matrix(gse81076.nz)))
sce <- calculateQCMetrics(sce, feature_controls=list(Spikes=spikes))
isSpike(sce) <- spikes

In [38]:
clusters <- quickCluster(sce, get.spikes=TRUE, min.size=120)
sce <- computeSumFactors(sce, sizes=c(10, 20, 40, 60), positive=T,
                         assay.type='counts', clusters=clusters)
summary(sizeFactors(sce))
sce <- normalize(sce)

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
 0.2702  0.5364  0.7982  1.0000  1.2371  6.9775 

Warning message in .local(object, ...):
“spike-in transcripts in '' should have their own size factors”

In [39]:
gse81076.norm <- data.frame(exprs(sce))

In [40]:
gse81076.norm$gene_id <- rownames(gse81076.df[keep_genes, ])
gse81076.norm$gene_id <- gsub(gse81076.norm$gene_id,
                              pattern="__chr[0-9X]+", replacement="")

In [43]:
write.table(gse81076.norm, sep='\t',
             file='Data/GSE81076_SFnorm.tsv',
             quote=FALSE, row.names=FALSE, col.names=TRUE)

write.table(gse81076.meta, sep="\t",
            file="Data/GSE81076_metadata.tsv",
            quote=FALSE, row.names=F, col.names=TRUE)

In [44]:
##############
## GSE85241 ##
##############
# clear environment and invoke garbage collector
rm(list=ls())
gc()

used    (Mb)  gc trigger (Mb)  max used  (Mb) 
Ncells 3858040 206.1  5684620   303.6   5684620 303.6
Vcells 3451751  26.4 87010348   663.9 108762935 829.8

In [45]:
gse85241 <- 'GSE85241_cellsystems_dataset_4donors_updated.csv'
if (!file.exists(gse85241)) { download.file("ftp://ftp.ncbi.nlm.nih.gov/geo/series/GSE85nnn/GSE85241/suppl/GSE85241%5Fcellsystems%5Fdataset%5F4donors%5Fupdated%2Ecsv%2Egz", 
                                            gse85241)}

In [47]:
gse85241.df <- read.table(gse85241, sep='\t', h=T, stringsAsFactors=F)
gse85241.df$gene_id <- rownames(gse85241.df)

In [48]:
head(gse85241.df)

D28.1_1  D28.1_2  D28.1_3  D28.1_4  D28.1_5 D28.1_6 D28.1_7
A1BG-AS1__chr19 0.000000 0.000000 0.000000 0.000000 0       0       0      
A1BG__chr19     0.000000 0.000000 1.001958 1.001958 0       0       0      
A1CF__chr10     6.071431 0.000000 2.007853 6.071431 0       0       0      
A2M-AS1__chr12  0.000000 0.000000 0.000000 0.000000 0       0       0      
A2ML1__chr12    0.000000 0.000000 0.000000 0.000000 0       0       0      
A2M__chr12      0.000000 5.049473 0.000000 0.000000 0       0       0      
                D28.1_8 D28.1_9 D28.1_10 ⋯ D30.8_88 D30.8_89 D30.8_90 D30.8_91 
A1BG-AS1__chr19 0       0       0        ⋯ 0.000000 0.000000 0.000000  0.000000
A1BG__chr19     0       0       0        ⋯ 0.000000 0.000000 0.000000  0.000000
A1CF__chr10     0       0       0        ⋯ 1.001958 7.097484 3.017717  0.000000
A2M-AS1__chr12  0       0       0        ⋯ 0.000000 2.007853 0.000000  1.001958
A2ML1__chr12    0       0       0        ⋯ 0.000000 0.000000 0.000000  0.000000
A2M__chr12      0       0       0        ⋯ 0.000000 0.000000 0.000000 11.243324
                D30.8_92 D30.8_93 D30.8_94 D30.8_95 D30.8_96 gene_id        
A1BG-AS1__chr19 0.000000 0        0.000000 0        0        A1BG-AS1__chr19
A1BG__chr19     0.000000 0        2.007853 0        0        A1BG__chr19    
A1CF__chr10     3.017717 0        0.000000 0        0        A1CF__chr10    
A2M-AS1__chr12  0.000000 0        0.000000 0        0        A2M-AS1__chr12 
A2ML1__chr12    0.000000 0        0.000000 0        0        A2ML1__chr12   
A2M__chr12      0.000000 0        7.097484 0        0        A2M__chr12

In [49]:
# gene IDs are located in column X for these data
colnames(gse85241.df) <- gsub(colnames(gse85241.df), pattern="X",
                              replacement="gene_id")

In [50]:
donor.id <-unlist(lapply(strsplit(colnames(gse85241.df)[1:(dim(gse85241.df)[2]-1)],
                                  fixed=T, split="."), 
                         FUN=function(x) paste0(x[1])))

In [51]:
plate.id <- unlist(lapply(strsplit(colnames(gse85241.df)[1:(dim(gse85241.df)[2]-1)],
                                   fixed=T, split="."),
                          FUN=function(x) paste0(x[2])))

In [52]:
protocol.id <- rep('CELseq2', dim(gse85241.df)[2]-1)
study.id <- rep('GSE85241', dim(gse85241.df)[2]-1)

In [53]:
gse85241.meta <- data.frame(list('Donor' = donor.id,
                                 'Plate'= plate.id,
                                 'Protocol' = protocol.id,
                                 'Study' = study.id,
                                 'Sample' = colnames(gse85241.df)[1:(dim(gse85241.df)[2]-1)]))

In [54]:
rownames(gse85241.meta) <- colnames(gse85241.df)[1:(dim(gse85241.df)[2]-1)]

In [56]:
write.table(gse85241.meta,
            file="Data/GSE85241_metadata.tsv",
            sep="\t", quote=FALSE, row.names=FALSE)

In [57]:
# set gene IDs as rownames, remove gene ID column
# remove duplicated gene IDs

In [58]:
gse85241.df$gene_id <- gsub(gse85241.df$gene_id,
                            pattern="__chr[0-9X]+", replacement="")
gse85241.df <- gse85241.df[!duplicated(gse85241.df$gene_id), ]
rownames(gse85241.df) <- gse85241.df$gene_id
gse85241.df <- gse85241.df[, 1:(dim(gse85241.df)[2]-1)]

In [59]:
# remove cells and genes with all 0's
gene_sparsity <- (apply(gse85241.df == 0, MARGIN = 1, sum)/dim(gse85241.df)[2])
keep_genes <- gene_sparsity < 0.9
gse85241.nz <- gse85241.df[keep_genes, ]

In [60]:
cell_sparsity <- apply(gse85241.nz == 0, MARGIN = 2, sum)/dim(gse85241.nz)[1]
keep_cells <- cell_sparsity < 0.8
dim(gse85241.nz[, keep_cells])
gse85241.nz <- gse85241.nz[, keep_cells]
gse85241.nz <- apply(gse85241.nz, 2, as.integer)

[1] 10312  2331

In [61]:
spikes <- grepl(rownames(gse85241.df[keep_genes, ]),
                pattern='ERCC')
sce <- SingleCellExperiment(list(counts = as.matrix(gse85241.nz)))
sce <- calculateQCMetrics(sce, feature_controls=list(Spikes=spikes))
isSpike(sce) <- spikes

In [62]:
clusters <- quickCluster(sce, get.spikes=TRUE, min.size=120)
sce <- computeSumFactors(sce, sizes=c(10, 20, 40, 60), positive=T,
                         assay.type='counts', clusters=clusters)
summary(sizeFactors(sce))

In [ ]:
sce <- normalize(sce)
gse85241.norm <- data.frame(exprs(sce))
gse85241.norm$gene_id <- rownames(gse85241.df[keep_genes, ])

In [ ]:
write.table(gse85241.norm, sep='\t',
            file='Data/GSE85241_SFnorm.tsv',
            quote=F, row.names=F, col.names=T)

In [ ]:
##############
## GSE86473 ##
##############
# clear environment and invoke garbage collector
rm(list=ls())
gc()

In [63]:
# the raw/processed counts table was not available for download from GEO for this data set
# these data were generated by mapping the original fastq's back to mm10, then using featureCounts to quantify
# against mm10 ensembl build 86
# data are contained in Pancreas/RawData for each cell type
alpha <- 'RawData/alpha-feature_counts.tsv.gz'

In [64]:
beta <- 'RawData/beta-feature_counts.tsv.gz'

In [65]:
delta <- 'RawData/delta-feature_counts.tsv.gz'

In [66]:
pp <- 'RawData/PP-feature_counts.tsv.gz'
# qc_out <- 'Pancreas/RawData/pancreas-smarseq2-qcout.tsv'

In [67]:
alpha.df <- read.table(alpha, sep='\t', h=T, stringsAsFactors=F)
beta.df <- read.table(beta, sep='\t', h=T, stringsAsFactors=F)
delta.df <- read.table(delta, sep='\t', h=T, stringsAsFactors=F)
pp.df <- read.table(pp, sep='\t', h=T, stringsAsFactors=F)

In [70]:
dim(alpha.df)
head(alpha.df)

[1] 58084   947

gene_id         alpha_ND_GSM2158106.star.dedup alpha_ND_GSM2158107.star.dedup
1 ENSG00000223972 0                              0                             
2 ENSG00000227232 0                              0                             
3 ENSG00000278267 0                              0                             
4 ENSG00000243485 0                              0                             
5 ENSG00000237613 0                              0                             
6 ENSG00000268020 0                              0                             
  alpha_ND_GSM2158108.star.dedup alpha_ND_GSM2158109.star.dedup
1 0                              0                             
2 0                              0                             
3 0                              0                             
4 0                              0                             
5 0                              0                             
6 0                              0                             
  alpha_ND_GSM2158110.star.dedup alpha_ND_GSM2158111.star.dedup
1 0                              0                             
2 0                              0                             
3 0                              0                             
4 0                              0                             
5 0                              0                             
6 0                              0                             
  alpha_ND_GSM2158112.star.dedup alpha_ND_GSM2158113.star.dedup
1 0                              0                             
2 0                              0                             
3 0                              0                             
4 0                              0                             
5 0                              0                             
6 0                              0                             
  alpha_ND_GSM2158114.star.dedup ⋯ alpha_T2D_GSM2159465.dedup
1 0                              ⋯ 0                         
2 0                              ⋯ 0                         
3 0                              ⋯ 0                         
4 0                              ⋯ 0                         
5 0                              ⋯ 0                         
6 0                              ⋯ 0                         
  alpha_T2D_GSM2159466.dedup alpha_T2D_GSM2159467.dedup
1 0                          0                         
2 0                          0                         
3 0                          0                         
4 0                          0                         
5 0                          0                         
6 0                          0                         
  alpha_T2D_GSM2159468.dedup alpha_T2D_GSM2159469.dedup
1 0                          0                         
2 0                          0                         
3 0                          0                         
4 0                          0                         
5 0                          0                         
6 0                          0                         
  alpha_T2D_GSM2159470.dedup alpha_T2D_GSM2159471.dedup
1 0                          0                         
2 0                          0                         
3 0                          0                         
4 0                          0                         
5 0                          0                         
6 0                          0                         
  alpha_T2D_GSM2159472.dedup alpha_T2D_GSM2159473.dedup
1 0                          0                         
2 0                          0                         
3 0                          0                         
4 0                          0                         
5 0                          0                         
6 0                          0                         
  alpha_T2D_GSM2159474.dedup
1 0                         
2 0                         
3 0      

In [71]:
# qc.df <- read.table(qc_out, sep='\t', h=F, stringsAsFactors=F)
data.list <- list("alpha"=alpha.df, "beta"=beta.df, "delta"=delta.df,
                  "gamma"=pp.df)

In [74]:
head(data.list,2)

$alpha
              gene_id alpha_ND_GSM2158106.star.dedup
1     ENSG00000223972                              0
2     ENSG00000227232                              0
3     ENSG00000278267                              0
4     ENSG00000243485                              0
5     ENSG00000237613                              0
6     ENSG00000268020                              0
7     ENSG00000240361                              0
8     ENSG00000186092                              0
9     ENSG00000238009                              0
10    ENSG00000239945                              0
11    ENSG00000233750                              0
12    ENSG00000268903                              0
13    ENSG00000269981                              0
14    ENSG00000239906                              0
15    ENSG00000241860                              0
16    ENSG00000222623                              0
17    ENSG00000241599                              0
18    ENSG00000279928                              0
19    ENSG00000279457                              0
20    ENSG00000273874                              0
21    ENSG00000228463                              0
22    ENSG00000241670                              0
23    ENSG00000236679                              0
24    ENSG00000236743                              0
25    ENSG00000236601                              0
26    ENSG00000237094                              0
27    ENSG00000269732                              0
28    ENSG00000278566                              0
29    ENSG00000224813                              0
30    ENSG00000233653                              0
31    ENSG00000250575                              0
32    ENSG00000278757                              0
33    ENSG00000230021                              0
34    ENSG00000235146                              0
35    ENSG00000225972                             24
36    ENSG00000225630                             13
37    ENSG00000237973                             23
38    ENSG00000278791                              0
39    ENSG00000229344                              1
40    ENSG00000240409                              0
41    ENSG00000248527                             36
42    ENSG00000198744                              0
43    ENSG00000268663                              0
44    ENSG00000273547                              0
45    ENSG00000283574                              0
46    ENSG00000229376                              0
47    ENSG00000228327                              0
48    ENSG00000223181                              0
49    ENSG00000229905                              0
50    ENSG00000237491                              0
51    ENSG00000230092                              0
52    ENSG00000177757                              0
53    ENSG00000228794                             88
54    ENSG00000225880                              0
55    ENSG00000230368                              0
56    ENSG00000234711                              0
57    ENSG00000283040                              0
58    ENSG00000272438                              0
59    ENSG00000230699                              0
60    ENSG00000241180                              0
61    ENSG00000223764                              0
62    ENSG00000187634                              0
63    ENSG00000188976                              0
64    ENSG00000187961                              0
65    ENSG00000187583                              0
66    ENSG00000187642                              0
67    ENSG00000272512                              0
68    ENSG00000188290                              0
69    ENSG00000187608                              0
70    ENSG00000231702                              0
71    ENSG00000224969                              0
72    ENSG00000188157                              0
73    ENSG00000242590                              0
74    ENSG00000217801                              2
75    ENSG00000273

In [75]:
gse86473.df <- Reduce(x=data.list,
                      f=function(x, y) merge(x, y, by='gene_id'))

In [ ]:
# remove .dedup suffix
samp.names <- unlist(lapply(strsplit(colnames(gse86473.df), fixed=T,
                                     split="."), 
                            FUN=function(x) paste0(x[1])))
colnames(gse86473.df) <- tolower(samp.names)

gse86473.meta <- read.table('Pancreas/RawData/GSE86473_experimental_design.tsv',
                            sep='\t', h=T, stringsAsFactors=F)
gse86473.meta$Sample <- tolower(gse86473.meta$Sample)
gse86473.meta$Study <- "GSE86473"

In [ ]:
# capitalize first letter of cell labels

gse86473.meta$CellType <- paste(toupper(substr(gse86473.meta$CellType, 1, 1)),
                                substr(gse86473.meta$CellType, 2, nchar(gse86473.meta$CellType)), sep="")

write.table(gse86473.meta,
            "Pancreas/Data/GSE86473_metadata.tsv",
            sep="\t", quote=FALSE, row.names=FALSE)

rownames(gse86473.df) <- gse86473.df$gene_id

In [ ]:
# need to map ensemlb gene ids to hgnc symbols to match up with other Pancreas data sets
ensembl <- useEnsembl(biomart='ensembl', dataset='hsapiens_gene_ensembl', GRCh=37)
gene_symbol <- getBM(attributes=c('ensembl_gene_id', 'external_gene_name'),
                     filters='ensembl_gene_id', mart=ensembl,
                     values=gse86473.df$gene_id)
dat <- merge(gse86473.df, gene_symbol,
             by.x='gene_id', by.y='ensembl_gene_id')
gene_symbols <- dat$external_gene_name
gse86473.df <- as.data.frame(append(dat[, -1],
                                    list(gene_id=gene_symbols),
                                    after=0))

In [ ]:
# unset hgnc_symbol as a factor and remove duplicated IDs
gse86473.df$gene_id <- as.character(gse86473.df$gene_id)
gse86473.df <- gse86473.df[!duplicated(gse86473.df$gene_id), ]

In [ ]:
# set the hgnc symbols as rownames and size factor normalize counts table
rownames(gse86473.df) <- gse86473.df$gene_id
gse86473.df <- gse86473.df[, 2:(dim(gse86473.df)[2]-1)]

In [ ]:
# remove cells and genes with all 0's
gene_sparsity <- (apply(gse86473.df == 0, MARGIN = 1, sum)/dim(gse86473.df)[2])
keep_genes <- gene_sparsity < 0.9
dim(gse86473.df[keep_genes, ])
gse86473.nz <- gse86473.df[keep_genes, ]

In [ ]:
cell_sparsity <- apply(gse86473.nz == 0, MARGIN = 2, sum)/dim(gse86473.nz)[1]
keep_cells <- cell_sparsity < 0.8
dim(gse86473.nz[, keep_cells])
gse86473.nz <- gse86473.nz[, keep_cells]
gse86473.nz <- apply(gse86473.nz, 2, as.integer)

In [ ]:
sce <- SingleCellExperiment(list(counts = as.matrix(gse86473.nz)))
sce <- calculateQCMetrics(sce)
clusters <- quickCluster(sce, min.size=120)
sce <- computeSumFactors(sce, sizes=c(10, 20, 40, 60), positive=T,
                         assay.type='counts', clusters=clusters)
summary(sizeFactors((sce)))

In [ ]:
sce <- normalize(sce)
gse86473.norm <- data.frame(exprs(sce))
gse86473.norm$gene_id <- rownames(gse86473.df[keep_genes, ])

In [ ]:
write.table(gse86473.norm, sep='\t',
            file='Pancreas/Data/GSE86473_SFnorm.tsv',
            quote=F, row.names=F, col.names=T)

In [ ]:
#################
## E-MTAB-5061 ##
#################
# clear environment and invoke garbage collector
rm(list=ls())
gc()

In [ ]:
# the download file contains columns of RPKM & counts
# need to pull out just the integer gene count columns
emtab_combined <- "Pancreas/RawData/EMTAB5061_rpkm_counts.txt.zip"
if(!file.exists(emtab_combined)){ download.file("https://www.ebi.ac.uk/arrayexpress/experiments/E-MTAB-5061/files/E-MTAB-5061.processed.1.zip",
              emtab_combined)}

In [ ]:
# need to unzip via a system call
unzip.file <- "Pancreas/RawData/pancreas_refseq_rpkms_counts_3514sc.txt"
if(!file.exists(unzip.file)) {system(paste0("unzip ", emtab_combined, " -d ", "Pancreas/RawData/"))}

emtab.df <- read.table(unzip.file,
                       h=FALSE, sep="\t", stringsAsFactors=F)

col.names <- unlist(read.table("Pancreas/RawData/pancreas_refseq_rpkms_counts_3514sc.txt",
                        h=FALSE, sep="\t", stringsAsFactors=F, comment.char="", nrows = 1))

In [ ]:
# first 2 columns are gene symbol and NCBI ID
# because of the way that this table is constructed, there are two cells for each column, but they
# are not contiguous.  Therefore, the sample names need to be read in separately to the counts/rpkm table

emtab5061.df <- emtab.df[, c(1, 3517:dim(emtab.df)[2])]
colnames(emtab5061.df) <- gsub(col.names, pattern="#samples", replacement="gene_id")

In [ ]:
# download sdrf file direct from arrayExpress
emtab.file <- "Pancreas/RawData/E-MTAB-5061.sdrf.txt"
if(!file.exists(emtab.file)) {download.file("https://www.ebi.ac.uk/arrayexpress/files/E-MTAB-5061/E-MTAB-5061.sdrf.txt",
              emtab.file)}

emtab.sdrf <- read.table("Pancreas/RawData/E-MTAB-5061.sdrf.txt",
                         h=TRUE, sep="\t", stringsAsFactors=FALSE)

In [ ]:
# construct the appropriate meta data columns, i.e. donor, plate, protocol, study
emtab.meta <- emtab.sdrf[, c("Assay.Name", "Characteristics.cell.type.", "Characteristics.individual.")]
colnames(emtab.meta) <- c("Sample", "CellType", "Donor")
emtab.meta$Study <- "E-MTAB-5061"
emtab.meta$Protocol <- "SmartSeq2"

In [ ]:
# remove the marked low quality cells
remove.cells <- unique(emtab.sdrf$Assay.Name[emtab.sdrf$Characteristics.single.cell.well.quality. == "low quality cell"])
emtab5061.df <- emtab5061.df[, !colnames(emtab5061.df) %in% remove.cells]
emtab.meta <- emtab.meta[!emtab.meta$Sample %in% remove.cells, ]
rownames(emtab.meta) <- emtab.meta$Sample

emtab.meta$CellType <- gsub(emtab.meta$CellType,
                            pattern=" cell", replacement="")

emtab.meta$CellType <- paste(toupper(substr(emtab.meta$CellType, 1, 1)),
                             substr(emtab.meta$CellType, 2, nchar(emtab.meta$CellType)), sep="")

write.table(emtab.meta,
            file="Pancreas/Data/E-MTAB-5061_metadata.tsv",
            sep="\t", quote=FALSE, row.names=FALSE)

In [ ]:
# remove duplicated gene IDs and set to rownames
emtab5061.df <- emtab5061.df[!duplicated(emtab5061.df$gene_id), ]
rownames(emtab5061.df) <- emtab5061.df$gene_id

emtab5061.df <- emtab5061.df[, -1]

In [ ]:
# remove cells and genes with all 0's
gene_sparsity <- (apply(emtab5061.df == 0, MARGIN = 1, sum)/dim(emtab5061.df)[2])
keep_genes <- gene_sparsity < 0.9
dim(emtab5061.df[keep_genes, ])
emtab5061.nz <- emtab5061.df[keep_genes, ]

In [ ]:
cell_sparsity <- apply(emtab5061.nz == 0, MARGIN = 2, sum)/dim(emtab5061.nz)[1]
keep_cells <- cell_sparsity < 0.8
dim(emtab5061.nz[, keep_cells])
emtab5061.nz <- emtab5061.nz[, keep_cells]
emtab5061.nz <- apply(emtab5061.nz, 2, as.integer)

In [ ]:
spikes <- grepl(x=rownames(emtab5061.df[keep_genes, ]), pattern="ERCC")
sce <- SingleCellExperiment(list(counts = as.matrix(emtab5061.nz)))
sce <- calculateQCMetrics(sce, feature_controls=list(Spikes=spikes))
isSpike(sce) <- spikes

In [ ]:
clusters <- quickCluster(sce, min.size=120)
sce <- computeSumFactors(sce, sizes=c(10, 20, 40, 60), positive=T,
                         assay.type='counts', clusters=clusters)
summary(sizeFactors((sce)))
sce <- normalize(sce)
emtab.norm <- data.frame(exprs(sce))
emtab.norm$gene_id <- rownames(emtab5061.df[keep_genes, ])

In [ ]:
write.table(emtab.norm,
            file="Pancreas/Data/E-MTAB-5061_SFnorm.tsv",
            quote=FALSE, row.names=FALSE, sep="\t")

In [ ]:
# clear the R environment in case this script is directly sourced
rm(list=ls())
gc()